In [1]:
!pip install Cython==0.28

In [2]:
!pip install shap

In [3]:
!pip install anchor

In [4]:
!pip install rbo

In [5]:
!pip install dlukes_rbo

ERROR: Could not find a version that satisfies the requirement dlukes_rbo (from versions: none)
ERROR: No matching distribution found for dlukes_rbo


In [6]:
RANDOM_SEED = 1

import os
import re
import gc
import sys
import random
import json
import logging
import numpy as np
from numpy.random import RandomState
from collections import Counter, OrderedDict
import itertools
from pprint import pprint
#import pathos
# from multiprocessing import Pool, TimeoutError
from importlib import reload  
import ipykernel
import requests
# Alternative that works for both Python 2 and 3:
from requests.compat import urljoin
from notebook.notebookapp import list_running_servers


random.seed(RANDOM_SEED)
# np.random.seed(seed=RANDOM_SEED)
const_random_state = RandomState(RANDOM_SEED)
import pandas as pd

import sklearn
from sklearn.preprocessing import StandardScaler, MultiLabelBinarizer
from sklearn.metrics import classification_report, jaccard_score, precision_recall_fscore_support

import warnings
warnings.filterwarnings('ignore')
logging.getLogger().setLevel('CRITICAL')

import experiments_config
import ipyparams

#sys.path.append(experiments_config.SIGDIRECT_PATH)
# from associative_classifier import AssociativeClassifier

############ importing LIME   ############
# if experiments_config.LIME_PATH not in sys.path:
#     sys.path.append(experiments_config.LIME_PATH)

LIME_PATH = '/cshome/alamanik/barbetest/'
SIGDIRECT_PATH = '/cshome/alamanik/barbetest/sigdirect/'
sys.path.append(LIME_PATH)
sys.path.append(SIGDIRECT_PATH)

print(sys.path[-3:])

import lime
import lime.lime_tabular


############ importing XLIME  ############
# if experiments_config.XLIME_PATH not in sys.path:
#     sys.path.append(experiments_config.XLIME_PATH)
# import xlime as xlime
# import xlime.lime_tabular
############ importing SHAP   ############
#import shap
############ importing Anchor ############
import anchor
#import anchor.anchor_tabular

############ importing RBO metric ############
import rbo
#import dlukes_rbo

print('Hi 1', experiments_config)
print('Hi 2222222222222222222222222222')


<IPython.core.display.Javascript object>

['/cshome/alamanik/.ipython', '/cshome/alamanik/barbetest/', '/cshome/alamanik/barbetest/sigdirect/']
Hi 1 <module 'experiments_config' from '/cshome/alamanik/barbetest/experiments/experiments_config.py'>
Hi 2222222222222222222222222222


In [7]:
def _reload_libs():
    global lime
#     xlime = reload(xlime)
#     xlime.lime_tabular = reload(xlime.lime_tabular)
    lime = reload(lime)
    lime.lime_tabular = reload(lime.lime_tabular)

def get_notebook_name():
    kernel_id = re.search('kernel-(.*).json',
                          ipykernel.connect.get_connection_file()).group(1)
    servers = list_running_servers()
    print(list(servers))
    for ss in servers:
        response = requests.get(urljoin(ss['url'], 'api/sessions'),
                                params={'token': ss.get('token', '')})
        for nn in json.loads(response.text):
            if nn['kernel']['id'] == kernel_id:
                return nn['notebook']['path'].split('/')[-1]
    return "backup_file"
print(get_notebook_name())

[{'base_url': '/', 'hostname': 'localhost', 'notebook_dir': '/cshome/alamanik/barbetest', 'password': True, 'pid': 1412377, 'port': 8078, 'secure': False, 'sock': '', 'token': '12345678', 'url': 'http://localhost:8078/'}]
backup_file


# Load & Pre-process Data

In [8]:
def get_train_df(filename, has_index, header_index=None):
    df = pd.read_csv(filename, sep=',', header=header_index, na_values='?')
    if has_index:
        df = df.drop(df.columns[0], axis=1)
    return df

def get_test_df(filename, has_index, header_index=None):
    df = pd.read_csv(filename, sep=',', header=header_index, na_values='?')
    if has_index:
        df = df.drop(df.columns[0], axis=1)
    return df

def preprocess_data(train_df, test_df, class_index, dataset_name):
    # removing class label, so we can call get_dummies on the rest
    train_df.rename(columns={list(train_df.columns)[class_index]:'class'}, inplace=True)
    print(train_df)
    print({list(train_df.columns)[class_index]:'class'})
    train_class = train_df['class']
    print(train_class)
    train_df.drop(columns=['class'], inplace=True)
    print(train_df)
    
    test_df.rename(columns={list(test_df.columns)[class_index]:'class'}, inplace=True)
    test_class = test_df['class']
    test_df.drop(columns=['class'], inplace=True)

    # process categorical data
    infer_types = []
    df = pd.concat([train_df, test_df])     #Now they no class column

    for column in df.columns:
        if df[column].dtype=='object':
            infer_types.append("{}_CAT".format(column))
        else:
            infer_types.append("{}_NUM".format(column))
    datasets_info_dict[dataset_name]['_NUM'] = sum(['_NUM' in x for x in infer_types])
    datasets_info_dict[dataset_name]['_CAT'] = sum(['_CAT' in x for x in infer_types])
#     print('INFER_TYPES:', infer_types)
    
    df = pd.get_dummies(df)
    train_df = df[:train_df.shape[0]]
    test_df  = df[train_df.shape[0]:]

    print(train_df)
    print(test_df)
    assert set(train_df.columns)==set(test_df.columns)

    # process numerical data (standardization is independent[?] for train/test splits)
    continuous_column_names = [x for x in list(train_df.columns) if not '_' in str(x)]
    print(continuous_column_names)
    for column in continuous_column_names:
        # standardazing the column
        scaler = StandardScaler()
        train_df[column] = scaler.fit_transform(train_df[column].to_numpy().reshape((-1,1)))
        test_df[column]  = scaler.transform(test_df[column].to_numpy().reshape((-1,1)))
        
        # set NaN to 0
        train_df[column].fillna(0., inplace=True)
        test_df[column].fillna(0., inplace=True)
        
    train_df['class'] = train_class
    test_df['class']  = test_class
    
    print(train_df)
    print(test_df)
    return train_df, test_df
    
def get_data(dataset_name, dataset_info):
    # input: name of the dataset, and a dictionary containing its info
    # process input arguments
    ## TA: If file_counts is 2, then train file and test filenames are separated. If 1, then 1 single fine
    file_counts  = 2 if dataset_info['SEPARATE_FILES'] else 1
    class_index  = dataset_info['CLASS_INDEX']
    has_index    = dataset_info['HAS_INDEX']
    header_index = dataset_info['HEADER_ROW_NUMBER']
    
    # set train/test filenames
    if file_counts==2:
        filenames = [os.path.join(DATA_ROOT_DIR, dataset_info['FOLDER_NAME'], dataset_info['TRAIN_FILENAME']), 
                     os.path.join(DATA_ROOT_DIR, dataset_info['FOLDER_NAME'], dataset_info['TEST_FILENAME'])]
    else:
        filenames = [os.path.join(DATA_ROOT_DIR, dataset_info['FOLDER_NAME'], dataset_info['COMBINED_FILENAME'])]


    print(filenames)
    filenames = ['/cshome/alamanik/barbetest/dataset/glass.data']
    
    if file_counts==1:
        # load from file
        df = get_train_df(filenames[0], has_index, header_index)
        # shuffle
        df = df.sample(frac=1, random_state=const_random_state)

        train_size = int(df.shape[0] * TRAIN_RATIO)
        train_df = df.iloc[:train_size]
        test_df  = df.iloc[train_size:]
        
    else:
        # load from file
        train_df = get_train_df(filenames[0], has_index, header_index)
        test_df  = get_test_df(filenames[1], has_index, header_index)
        # shuffle
        train_df = train_df.sample(frac=1, random_state=const_random_state)
        test_df  = test_df.sample(frac=1, random_state=const_random_state)

    # some of the preprocessing (one hot encoding + missing values + standardisation)
    dataset_info['initial_features'] = train_df.shape[1] -1
    
    train_df, test_df = preprocess_data(train_df, test_df, class_index, dataset_name)
    
    dataset_info['features'] = train_df.shape[1] -1
    dataset_info['initial_train_size'] = train_df.shape[0]
    dataset_info['initial_test_size'] = test_df.shape[0]
    dataset_info['original_train_df'] = train_df.copy()
    dataset_info['original_test_df']  = test_df.copy()
    
    if shrink_train_size and train_df.shape[0]>desired_train_size:
        train_df = train_df[:desired_train_size]
    if shrink_test_size  and test_df.shape[0]>desired_test_size:
        test_df = test_df[:desired_test_size]
    dataset_info['train_size'] = train_df.shape[0]
    dataset_info['test_size'] = test_df.shape[0]
        
    return train_df, test_df

# Interpretable Models

In [9]:
def get_clf(train_df, clf_type, info=None):
    if clf_type.lower()=='dt':
        return get_clf_dt(train_df, info['max_explanation_size'])
    if clf_type.lower()=='lr':
        return get_clf_lr(train_df, info['max_explanation_size'])
    raise Exception('Wrong interpretable model, select from "lr", "dt"')

def get_features(classifier_type, clf, row, info_dict):
    if classifier_type=='sd':
        clf_features = get_features_sd(clf, row)
    elif classifier_type=='dt':
        clf_features = get_features_dt(clf, row)
    elif classifier_type=='lr':
        clf_features = get_features_lr(clf, row, 
                                       info_dict['max_features'], 
                                       info_dict['num_labels'], 
                                       info_dict['predicted_label_index'])
    else:
        print('Incorrect classifier type. terminating ...', classifier_type)
        raise Exception("Incorrect classifier type")
    return clf_features

## 1. Decision Tree

In [10]:
def get_clf_dt(train_df, max_depth):
    clf = sklearn.tree.DecisionTreeClassifier(random_state=const_random_state, max_depth=max_depth)
    clf.fit(train_df.drop('class', axis=1), train_df['class'])
    return clf

def test_classifier_dt(clf, test_df):
    predictions = clf.predict(test_df.drop('class', axis=1))    
    acc = sklearn.metrics.accuracy_score(test_df['class'], predictions)
    return acc

def get_features_dt(clf, row):
    feature = clf.tree_.feature
    print('Inside: get_features_dt, feature = ', feature)
    leave_id = clf.apply(row.values.reshape(1, -1))
    #print(leave_id)
    node_indicator = clf.decision_path([row])
    #print(node_indicator)
    features = OrderedDict() # using as an ordered set
    node_index = node_indicator.indices[node_indicator.indptr[0]:node_indicator.indptr[1]]
#     node_index = node_indicator.indices[:] #node_indicator.indptr[0]:node_indicator.indptr[1]]
    #print(node_index)

    for node_id in node_index:
        if leave_id[0] == node_id:  # <-- changed != to ==
            continue # <-- comment out
        else: # < -- added else to iterate through decision nodes
#             features.append(feature[node_id]+1)
            if feature[node_id]+1 not in features:
                features[feature[node_id]+1] = None
#             else:
#                 print('redundant!!!')
    #print(features)
    final_features = [*features]
    print('final_features = ', final_features)
#     print(final_features)
    return final_features

def get_dt_avg_explanation(dt_clf, train_df):
    # find the depth for each training instance, and then return the average among them
#     decision_paths = dt_clf.decision_path(train_df).toarray()
#     uniques = np.unique(decision_paths, axis=1)
#     print(decision_paths[:5])
#     print(np.count_nonzero(decision_paths, axis=1).max()-1, np.count_nonzero(decision_paths, axis=1).min()-1)
#     return np.count_nonzero(decision_paths, axis=1).mean() - 1 # they all have an extra node which is the leaf
    lens = 0
    print('*** ', dt_clf)
    print('*** ', train_df)
    for _,row in train_df.iterrows():
        exp = get_features_dt(dt_clf, row)
        lens += len(exp)
    return lens/train_df.shape[0]

## 2. Logistic Regression

In [11]:
def get_clf_lr(train_df, max_features):
    try_cs1 = np.arange(1.,0,-.1)
    try_cs2 = np.arange(.1,0,-.01)
    try_cs3 = np.arange(.01,0,-.001)
    
    done = False
    for c in try_cs1:
        temp_clf = sklearn.linear_model.LogisticRegression(random_state=const_random_state, penalty='l1', fit_intercept=True, C=c, n_jobs=-1, solver='liblinear')
        temp_clf.fit(train_df.drop('class', axis=1), train_df['class'])
        lengths = [len(x.nonzero()[0]) for x in temp_clf.coef_]
        if np.max(lengths) <= max_features:
            done = True
            break
    if done:
        return temp_clf
    for c in try_cs2:
        temp_clf = sklearn.linear_model.LogisticRegression(random_state=const_random_state, penalty='l1', fit_intercept=True, C=c, n_jobs=-1, solver='liblinear')
        temp_clf.fit(train_df.drop('class', axis=1), train_df['class'])
        lengths = [len(x.nonzero()[0]) for x in temp_clf.coef_]
        if np.max(lengths) <= max_features:
            done = True
            break
    if done:
        return temp_clf
    for c in try_cs3:
        temp_clf = sklearn.linear_model.LogisticRegression(random_state=const_random_state, penalty='l1', fit_intercept=True, C=c, n_jobs=-1, solver='liblinear')
        temp_clf.fit(train_df.drop('class', axis=1), train_df['class'])
        lengths = [len(x.nonzero()[0]) for x in temp_clf.coef_]
        if np.max(lengths) <= max_features:
            done = True
            break
#     print('c:', c)
    return temp_clf
    
def test_classifier_lr(clf, test_df):
    predictions = clf.predict(test_df.drop('class', axis=1))    
    acc = sklearn.metrics.accuracy_score(test_df['class'], predictions)
    return acc

def get_features_lr(clf, row, max_features, num_classes, label_index):
    if num_classes<=2:
        idx = 0
    else:
        idx = label_index
    all_params = clf.coef_
    return set(np.where(all_params[idx]!=0.)[0]+1)
#     return set(np.argsort(all_params[idx])[:].tolist())

def get_lr_avg_explanation(clf, train_df):
    return max([len(x.nonzero()[0]) for x in clf.coef_])

# Global variables

In [12]:
# global variables
shrink_train_size = True
desired_train_size = 100

shrink_test_size = True
desired_test_size = 100

# used if data is not already split
TRAIN_RATIO = 0.75

PROCESS_COUNT = 50

# compute averages over all instances, or over the ones that the labels agree
fidelity_division = True

# how many runs to make sure fidelity is respected in BARBE/XLIME
REPEAT_COUNT = 1

DATA_ROOT_DIR = experiments_config.DATA_ROOT_DIR

datasets_info_dict = experiments_config.all_datasets_info_dict.copy()

datasets_info_dict = {
                    'glass':experiments_config.all_datasets_info_dict['glass'],
#                      'wine':experiments_config.all_datasets_info_dict['wine'],
#                      'hungarian':experiments_config.all_datasets_info_dict['hungarian'],
#                      'hepatitis':experiments_config.all_datasets_info_dict['hepatitis'],
#                      'poker':experiments_config.all_datasets_info_dict['poker'],
                     }


info = {'max_explanation_size':5}

remove_datasets = [
    'online_shoppers_intention', # slow with 1k!
    'breast-cancer', # very slow even in 200!, but good results!
    'car', # has a small tree! f1=55, fidel:82
    'nursery', # precision=1, recall=.5
    'adult', # slow, 1k won't finish in 2h
]
# remove_datasets = ['online_shoppers_intention']

for x in remove_datasets:
    if x in  datasets_info_dict:
        del datasets_info_dict[x]

datasets_info_dict

{'glass': {'FOLDER_NAME': 'glass',
  'SEPARATE_FILES': False,
  'TRAIN_FILENAME': None,
  'TEST_FILENAME': None,
  'COMBINED_FILENAME': 'glass.data',
  'CLASS_INDEX': -1,
  'HAS_INDEX': True,
  'HEADER_ROW_NUMBER': None}}

# Experiments

## 1. Datasets Evaluation

### Goals of these experiments:
I want to know more about the datasets I use, and have the enough knowledge about them so I could use different type of datasets (in terms of size/feature/complexity) in my experiments.

Given say onnly 10 features, we can have feature spaces that are very complex, or very simple. The same thing can happen when we have 100 features. So, I need datasets that cover all such cases.


I plan to use train sets to a) train the classifiers, and b) tune BARBE. Since this is my own training, I can limit the size of the train set used in the experiments to a reasonable number like 200.
#### Obtaining General info about datasets
1. Number of features, train instances, test instances
2. 

#### Understanding how different interpretable classifiers work w.r.t. these datasets
1. Classifier accuracy on these datasets
2. info unique to each classifier:
    2.1. DT: average depth of the tree 
    2.2. Rule-based: average number of rules for each instance


In [13]:
print(datasets_info_dict.items())
for dataset, dataset_info in datasets_info_dict.items():
    print('---', dataset)
    print('---', dataset_info)
    train_df, test_df = get_data(dataset, dataset_info)
    dataset_info['train_df'] = train_df
    dataset_info['test_df'] = test_df
    dataset_info['nclasses'] = train_df['class'].unique().shape[0]
    
print(datasets_info_dict.items())

dict_items([('glass', {'FOLDER_NAME': 'glass', 'SEPARATE_FILES': False, 'TRAIN_FILENAME': None, 'TEST_FILENAME': None, 'COMBINED_FILENAME': 'glass.data', 'CLASS_INDEX': -1, 'HAS_INDEX': True, 'HEADER_ROW_NUMBER': None})])
--- glass
--- {'FOLDER_NAME': 'glass', 'SEPARATE_FILES': False, 'TRAIN_FILENAME': None, 'TEST_FILENAME': None, 'COMBINED_FILENAME': 'glass.data', 'CLASS_INDEX': -1, 'HAS_INDEX': True, 'HEADER_ROW_NUMBER': None}
['/cshome/motalleb/DM/UCI/archive.ics.uci.edu/ml/machine-learning-databases/glass/glass.data']
           1      2     3     4      5     6      7     8     9  class
108  1.52222  14.43  0.00  1.00  72.67  0.10  11.52  0.00  0.08      2
206  1.51645  14.94  0.00  1.87  73.11  0.00   8.67  1.38  0.00      7
106  1.53125  10.73  0.00  2.10  69.81  0.58  13.30  3.15  0.28      2
107  1.53393  12.30  0.00  1.00  70.16  0.12  16.19  0.00  0.24      2
51   1.51926  13.20  3.33  1.28  72.36  0.60   9.14  0.00  0.11      1
..       ...    ...   ...   ...    ...   ...  

In [14]:
for dataset, dataset_info in datasets_info_dict.items():
    ############ Decision Tree ############
    print('111')
    if 'dt_clf' not in dataset_info:
        print('dt_clf')
        dt_clf = get_clf(dataset_info['original_train_df'], 'dt', info)
        avg_explanation_len = get_dt_avg_explanation(dt_clf, dataset_info['train_df'].drop(columns=['class']))
        print('avg_explanation_len = ', avg_explanation_len)
        dataset_info['dt_len'] = avg_explanation_len
        dataset_info['dt_acc'] = test_classifier_dt(dt_clf, dataset_info['test_df'])
        dataset_info['dt_clf'] = dt_clf
    ############ Logistic Regression ############
    if 'lr_clf' not in dataset_info:
        print('lr_clf')
        lr_clf = get_clf(dataset_info['original_train_df'], 'lr', info)
        avg_explanation_len = get_lr_avg_explanation(lr_clf, dataset_info['train_df'].drop(columns=['class']))
        dataset_info['lr_len'] = avg_explanation_len
        dataset_info['lr_acc'] = test_classifier_lr(lr_clf, dataset_info['test_df'])
        dataset_info['lr_clf'] = lr_clf
    print('222')
    
dataset_info

111
dt_clf
***  DecisionTreeClassifier(max_depth=5,
                       random_state=RandomState(MT19937) at 0x7FDA94B4D160)
***              1         2         3         4         5         6         7  \
108  1.172462  1.178967 -1.763019 -0.886022 -0.004176 -0.569697  1.663606   
206 -0.586593  1.761773 -1.763019  0.812563  0.540266 -0.705339 -0.200470   
106  3.925370 -3.049231 -1.763019  1.261614 -3.543053  0.081385  2.827836   
107  4.742401 -1.255103 -1.763019 -0.886022 -3.109974 -0.542569  4.718074   
51   0.270070 -0.226623  0.491208 -0.339351 -0.387761  0.108514  0.106939   
..        ...       ...       ...       ...       ...       ...       ...   
132 -0.074425  0.036211  0.931222 -0.534590 -0.226903  0.081385 -0.540582   
193 -0.360995  1.544649 -1.763019  1.066374  0.428903 -0.705339 -0.292039   
153 -0.693295  0.024784  0.538594 -0.456495  0.020571  0.094950 -0.429391   
166  0.956010 -2.706404 -0.605443  0.207320  0.948598  0.081385  1.729012   
160 -0.016501 -0.078

 -2  1 -2 -2  4  7 -2 -2 -2]
final_features =  [8, 4, 7, 1, 9]
Inside: get_features_dt, feature =  [ 7  3  6  0  0 -2 -2  8 -2 -2  0  1 -2 -2 -2  2  1  6 -2 -2 -2  6  8 -2
 -2  1 -2 -2  4  7 -2 -2 -2]
final_features =  [8, 4, 7, 1]
Inside: get_features_dt, feature =  [ 7  3  6  0  0 -2 -2  8 -2 -2  0  1 -2 -2 -2  2  1  6 -2 -2 -2  6  8 -2
 -2  1 -2 -2  4  7 -2 -2 -2]
final_features =  [8, 4, 3, 7, 2]
Inside: get_features_dt, feature =  [ 7  3  6  0  0 -2 -2  8 -2 -2  0  1 -2 -2 -2  2  1  6 -2 -2 -2  6  8 -2
 -2  1 -2 -2  4  7 -2 -2 -2]
final_features =  [8, 4, 7, 1, 9]
Inside: get_features_dt, feature =  [ 7  3  6  0  0 -2 -2  8 -2 -2  0  1 -2 -2 -2  2  1  6 -2 -2 -2  6  8 -2
 -2  1 -2 -2  4  7 -2 -2 -2]
final_features =  [8, 4, 3, 7, 2]
Inside: get_features_dt, feature =  [ 7  3  6  0  0 -2 -2  8 -2 -2  0  1 -2 -2 -2  2  1  6 -2 -2 -2  6  8 -2
 -2  1 -2 -2  4  7 -2 -2 -2]
final_features =  [8, 4, 7, 1, 9]
Inside: get_features_dt, feature =  [ 7  3  6  0  0 -2 -2  8 -2 -2  0  1 -2 -2 -

{'FOLDER_NAME': 'glass',
 'SEPARATE_FILES': False,
 'TRAIN_FILENAME': None,
 'TEST_FILENAME': None,
 'COMBINED_FILENAME': 'glass.data',
 'CLASS_INDEX': -1,
 'HAS_INDEX': True,
 'HEADER_ROW_NUMBER': None,
 'initial_features': 9,
 '_NUM': 9,
 '_CAT': 0,
 'features': 9,
 'initial_train_size': 160,
 'initial_test_size': 54,
 'original_train_df':             1         2         3         4         5         6         7  \
 108  1.172462  1.178967 -1.763019 -0.886022 -0.004176 -0.569697  1.663606   
 206 -0.586593  1.761773 -1.763019  0.812563  0.540266 -0.705339 -0.200470   
 106  3.925370 -3.049231 -1.763019  1.261614 -3.543053  0.081385  2.827836   
 107  4.742401 -1.255103 -1.763019 -0.886022 -3.109974 -0.542569  4.718074   
 51   0.270070 -0.226623  0.491208 -0.339351 -0.387761  0.108514  0.106939   
 ..        ...       ...       ...       ...       ...       ...       ...   
 201 -0.562204 -1.655068 -1.763019 -0.515066  3.101621  2.956999 -0.030414   
 64   1.020031  0.093349  0.76875

In [15]:
# print('Datasets:', len(experiments_config.all_datasets_info_dict), '-->', len(datasets_info_dict))
# for dataset, dataset_info in datasets_info_dict.items():
#     print(dataset)
#     pprint({x:y for (x,y) in dataset_info.items() if ('_df' not in x) and ('_clf' not in x)})
#     print()

In [16]:
# raise Exception("stop!")

## 2. Tuning BARBE

### Process each instance and extract explanations

In [17]:
def get_nonzero_features_lime(row, clf, num_features, explainer, num_labels, 
                              max_valid_features, predicted_label_index, num_samples, xlime_mode, seed):
    """ For a given class, return top k features"""
    random.seed(seed)
    np.random.seed(seed)
    classes = list(range(num_labels))
    print('** classes ', classes)
#     if isinstance(explainer, xlime.lime_tabular.LimeTabularExplainer):
#         print('Caller 1')
#         x = explainer.explain_instance(row.to_numpy(), 
#                                    clf.predict_proba, 
#                                    num_features=max_valid_features, 
#                                    labels=[predicted_label_index],
#                                    num_samples=num_samples,
#                                    classes=classes,
#                                    xlime_mode=xlime_mode,
#                                    model_regressor='alaki' # SigDirect
# #                                    model_regressor=sklearn.tree.DecisionTreeRegressor(
# #                                                        criterion="mae",
# #                                                        max_depth=max_valid_features, 
# #                                        )
# #                                   model_regressor=sklearn.linear_model.LinearRegression()
# #                                   model_regressor=GaussianNB()
#                                   )
# #         print(x)
#         fidelity = x.fidelity
#     else:
    print('Caller 2')
    x = explainer.explain_instance(row.to_numpy(), 
                               clf.predict_proba, 
                               num_features=max_valid_features, 
                               labels=[predicted_label_index],
                               num_samples=num_samples)
#         print(x.local_pred)
#         fidelity = 1.0
    if x.local_pred>=1.0/num_labels:
        fidelity = 1.0
    else:
        fidelity = 0.0
    feature_score_pairs = x.as_map()[predicted_label_index]
#     print('feature_score_pairs.shape', len(feature_score_pairs))
    feature_score_pairs = [(x[0]+1, x[1]) for x in feature_score_pairs if x[1]!=0.]
    feature_score_pairs = sorted(feature_score_pairs, key=lambda x:x[1], reverse=True)
    nonzero_features = [x[0] for x in feature_score_pairs[:max_valid_features]]

    if fidelity==0.0:##
        nonzero_features = []
    return nonzero_features, fidelity

def get_nonzero_features_anchor(row, clf, num_features, explainer, 
                              max_valid_features, predicted_label_index, num_samples, seed):
    """ For a given class, return top k features"""
    random.seed(seed)
    np.random.seed(seed)
    
#         def explain_instance(self, data_row, classifier_fn, threshold=0.95,
#                           delta=0.1, tau=0.15, batch_size=100,
#                           max_anchor_size=None,
#                           desired_label=None,
#                           beam_size=4, **kwargs):

#     print('shape:', row.to_numpy().shape)
    x = explainer.explain_instance(row.to_numpy().reshape(1,-1), 
                                   clf.predict, 
                                   max_anchor_size=max_valid_features, 
                                   desired_label=predicted_label_index,
#                                    num_samples=num_samples,
                                   coverage_samples=num_samples,
                                  )
#     print(x.names(), x.features())
    features = x.features()#[predicted_label_index]
    features = [x+1 for x in features]
#     feature_score_pairs = [(x[0]+1, x[1]) for x in feature_score_pairs if x[1]!=0.]
#     nonzero_features = [x[0] for x in feature_score_pairs]
    return features

def get_nonzero_features_shap(row, clf, num_features, explainer, 
                              max_valid_features, predicted_label_index, num_samples, seed):
    """ For a given class, return top k features"""
    random.seed(seed)
    np.random.seed(seed)
    x = explainer.shap_values(row, nsamples=num_samples)
    features_scores = x[predicted_label_index]
#     print(features_scores)
    sorted_features = sorted(list(enumerate(features_scores)), key=lambda x:abs(x[1]), reverse=True)
    ret = [x[0]+1 for x in sorted_features[:max_valid_features]]
    return ret

In [18]:
def evaluate_instance(args):    
    ((idx, row), clf, classifier_type, num_features, num_labels, 
                      explainer, num_samples, xlime_mode, seed, ordered_class_labels, method, max_features) = args
    print('Evaluating: ', ((idx, row), clf, classifier_type, num_features, num_labels, 
                      explainer, num_samples, xlime_mode, seed, ordered_class_labels, method, max_features))
    
    random.seed(seed)
    np.random.seed(seed)
#     print(idx)
    fidelity = 1
    predicted_label_index = ordered_class_labels.index(clf.predict(row.values.reshape(1, -1))[0])
    print(predicted_label_index, clf.predict(row.values.reshape(1, -1))[0])
    clf_features = get_features(classifier_type, clf, row, {'max_features':max_features, 'num_labels':num_labels, 'predicted_label_index':predicted_label_index})
    if method=="XLIME":
#         my_modes = [["FOURTEEN", "SIXTEEN"], ["SEVENTEEN", "EIGHTEEN"], "FIFTEEN" ]
#         my_modes = [["FOURTEEN", "SEVENTEEN"]] 
        my_modes = ["FOURTEEN", "SEVENTEEN", "SIXTEEN", "EIGHTEEN"]
        explainer_features = []
        temp_seed = seed
        for i in range(REPEAT_COUNT):
            b, fidelity = get_nonzero_features_lime(row, clf, num_features, 
                                                  explainer, num_labels, max_features,                                                      
                                                  predicted_label_index, num_samples, 
#                                                   ["FOURTEEN","FIFTEEN"],
                                                  my_modes[i] , # "FOURTEEN"
                                                  seed, # temp_seed, # seed, # 
                                                   )
            temp_seed += 11
            if fidelity==1.0:
#                 if i>0:
#                     print(i)
                if len(explainer_features)>0:
                    explainer_features.extend([x for x in b if x not in set(explainer_features)])
                else:
                    explainer_features = b
                break
        
        explainer_features = explainer_features[:max_features]
    elif method=="LIME":
        print('----')
        explainer_features, fidelity = get_nonzero_features_lime(row, clf, num_features, 
                                                  explainer, num_labels, max_features,                                                      
                                                  predicted_label_index, num_samples, xlime_mode,
                                                  seed)

    elif method=="ANCHOR":
        explainer_features = set(get_nonzero_features_anchor(row, clf, num_features, 
                                                  explainer, max_features, 
                                                  predicted_label_index, num_samples,
                                                  seed))
    elif method=="SHAP":
        explainer_features = set(get_nonzero_features_shap(row, clf, num_features, 
                                                  explainer, max_features, 
                                                  predicted_label_index, num_samples,
                                                  seed))
    else:
        raise Exception("Incorrect method selected", method)
#     print(idx, 
#           fidelity,
#           list(clf_features), 
#           list(explainer_features),
#           sum([x in clf_features for x in explainer_features])/len(explainer_features) if len(explainer_features)>0 else 0.0,
#           sum([x in explainer_features for x in clf_features])/len(clf_features) if len(clf_features)>0 else 0.0)
    fout.write("{}, {}, {}, {}\n".format(idx, 
                                         list(clf_features), 
                                         list(explainer_features), 
                                         sum([x in clf_features for x in explainer_features])/len(explainer_features) if len(explainer_features)>0 else 0.0,
                                         sum([x in explainer_features for x in clf_features])/len(clf_features) if len(clf_features)>0 else 0.0))
    return list(clf_features), list(explainer_features), fidelity
    

def evaluate_explanations_parallel(dataset_name, clf, train_df, test_df, classifier_type, num_samples, around_instance, seed, max_features, method='LIME', xlime_mode='ONE'):
    print('Function evaluate_explanations_parallel with params = ', dataset_name, clf, classifier_type, num_samples, around_instance, seed, max_features, method, xlime_mode)
    random.seed(1)
    np.random.seed(1)
    train_df2 = train_df.drop('class', axis=1)   #train_df2 and test_df2 is without class labels
    test_df2 = test_df.drop('class', axis=1)
    ordered_class_labels = sorted(list(set(train_df['class'].values)))
    print('train_df ordered_class_labels: ', ordered_class_labels)
    columns = list(train_df2.columns)
    categorical_features        = [x for x in columns if '_' in str(x)]
    categorical_feature_indices = [columns.index(x) for x in columns if '_' in str(x)]
    categorical_features_map    = {columns.index(x):x for x in columns if '_' in str(x)}
    
    all_features = train_df2.columns.values
    print('dataset:', dataset_name, 'method:', method, 'seed:', seed, 'num_samples:', num_samples, 'test size:', test_df2.shape)
    print('all_features')
    print(all_features)
    fout.write('dataset: {} method: {} seed: {} num_sampes: {} test size: {}\n'.format(dataset_name, method, seed, num_samples, test_df2.shape))
    if method=='XLIME':
#         discretizers = ['decile', 'eightile', 'sixile', 'quartile'] 
#         for i in range(4):
#             try:
        explainer = xlime.lime_tabular.LimeTabularExplainer(train_df2.values, 
                                                           categorical_features=categorical_feature_indices, 
                                                           feature_names=all_features,
                                                           verbose=False, 
                                                           class_names=ordered_class_labels,
                                                           mode='classification',
                                                           random_state=RandomState(seed), 
                                                           discretizer='decile',
#                                                            discretizer=discretizers[i],
    #                                                        training_labels=train_df['class'].values,
                                                           feature_selection='none'
                                                          )
#                 print(discretizers[i])
#                 break
#             except Exception as e:
#                 print(str(e))
#                 pass
    elif method=='LIME':
        print('My method is LIME')
        discretizers = ['decile', 'eightile', 'sixile', 'quartile'] 
        for i in range(1):
            try:
                explainer = lime.lime_tabular.LimeTabularExplainer(train_df2.values,  
                                                       categorical_features=categorical_feature_indices, 
                                                       feature_names=all_features,
                                                       verbose=False, 
                                                       class_names=ordered_class_labels,
                                                       mode='classification', 
                                                       sample_around_instance=around_instance, 
                                                       random_state=RandomState(seed),
                                                       discretizer=discretizers[i],
#                                                        training_labels=train_df['class'].values,
                                                      )
                print(explainer)
#                 print(discretizers[i])
                break
            except Exception as e:
                print(str(e))
                pass
    elif method=='ANCHOR':
#          def __init__(self, class_names, feature_names, data=None,
#                  categorical_names=None, ordinal_features=[]):
#         explainer = anchor_tabular.AnchorTabularExplainer(dataset.class_names, dataset.feature_names, 
#                                                           dataset.data, dataset.categorical_names)
        explainer = anchor.anchor_tabular.AnchorTabularExplainer(ordered_class_labels,
                                                       train_data=train_df2.values,  
                                                       categorical_names=categorical_features_map, 
                                                       feature_names=all_features,
#                                                        verbose=False, 
#                                                        class_names=ordered_class_labels, # error
#                                                        mode='classification',  # error
#                                                        sample_around_instance=around_instance,  # error
#                                                        random_state=RandomState(seed), # error
                                                       discretizer='decile'
                                                      )
#         explainer.fit(dataset.train, dataset.labels_train, dataset.validation, dataset.labels_validation)
#         split_idx = int(train_df.shape[0] * 0.75)
#         temp_train_df = train_df[:split_idx]
#         temp_valid_df = train_df[split_idx:]
#         print(temp_valid_df['class'].values)
#         explainer.fit(train_df.drop('class', axis=1).values, train_df['class'].values,
#                       train_df.drop('class', axis=1).values, train_df['class'].values,
#                       discretizer='decile')

    elif method=='SHAP':
        explainer = shap.KernelExplainer(clf.predict_proba, train_df2.values) #, link=<shap.common.IdentityLink object>, **kwargs)
    else:
        raise Exception("incorrect explanation method provided to evaluate_explanations:", method)
        
    num_labels = len(ordered_class_labels) # 0#max(train_df['class']) - train_df.shape[1]
    
    # modify this based on the type of the experiments (tuning --> train_df2)/(evaluating --> test_df2)
#     chosen_dataset = train_df2
    chosen_dataset = test_df2
    
    if method in ('XLIME', 'ANCHOR'):
        print('1', method)
        with pathos.multiprocessing.ProcessPool(ncpus=PROCESS_COUNT) as pool:
            ret = pool.map(evaluate_instance, zip(
                                                  chosen_dataset.iterrows(),
                                                  itertools.cycle([clf]),
                                                  itertools.cycle([classifier_type]),
                                                  itertools.cycle([chosen_dataset.shape[1]]),
                                                  itertools.cycle([num_labels]),
                                                  itertools.cycle([explainer]),
                                                  itertools.cycle([num_samples]),
                                                  itertools.cycle([xlime_mode]),
                                                  itertools.cycle([seed]),
                                                  itertools.cycle([ordered_class_labels]),
                                                  itertools.cycle([method]),
                                                  itertools.cycle([max_features])
                                                 ),                                                                          
                                             )
    else:
        print('2', method, ordered_class_labels, list(zip(
                                                  chosen_dataset.iterrows(),
                                                  itertools.cycle([clf]),
                                                  itertools.cycle([classifier_type]),
                                                  itertools.cycle([chosen_dataset.shape[1]]),
                                                  itertools.cycle([num_labels]),
                                                  itertools.cycle([explainer]),
                                                  itertools.cycle([num_samples]),
                                                  itertools.cycle([xlime_mode]),
                                                  itertools.cycle([seed]),
                                                  itertools.cycle([ordered_class_labels]),
                                                  itertools.cycle([method]),
                                                  itertools.cycle([max_features])
                                                 )))
        
        ret = map(evaluate_instance, zip(
                                                  chosen_dataset.iterrows(),
                                                  itertools.cycle([clf]),
                                                  itertools.cycle([classifier_type]),
                                                  itertools.cycle([chosen_dataset.shape[1]]),
                                                  itertools.cycle([num_labels]),
                                                  itertools.cycle([explainer]),
                                                  itertools.cycle([num_samples]),
                                                  itertools.cycle([xlime_mode]),
                                                  itertools.cycle([seed]),
                                                  itertools.cycle([ordered_class_labels]),
                                                  itertools.cycle([method]),
                                                  itertools.cycle([max_features])
                                                 ),                                                                          
                                             )
    all_clf_features, all_exp_features, fidelities = zip(*ret)
    print('--- Returned ', all_clf_features, all_exp_features, fidelities)
    return all_clf_features, all_exp_features, fidelities

In [19]:
# Evaluation functions
import rbo
def analyze_outputs(all_features, initial_all_clf_features, initial_all_exp_features, fidelities):
    random.seed(1)
    np.random.seed(1)
    if fidelity_division:
        all_clf_features = [x for x,fidel in zip(initial_all_clf_features, fidelities) if fidel]
        all_exp_features = [x for x,fidel in zip(initial_all_exp_features, fidelities) if fidel]
    else:
        all_clf_features = initial_all_clf_features
        all_exp_features = initial_all_exp_features
        
    print(len(all_clf_features), sum(fidelities))
#     print('shapes:', len(all_clf_features), len(all_exp_features))
    mlb = MultiLabelBinarizer()
    mlb.fit([[i+1] for i,x in enumerate(all_features)])
#     print('unique 1:', set(itertools.chain(*all_clf_features)))
#     print('unique 2:', set(itertools.chain(*all_exp_features)))
    print(classification_report(mlb.transform(all_clf_features), mlb.transform(all_exp_features), output_dict=True)['samples avg'])
    fout.write(str(classification_report(mlb.transform(all_clf_features), mlb.transform(all_exp_features), output_dict=True)['samples avg'])+'\n')

    print('f0.5-score:', precision_recall_fscore_support(mlb.transform(all_clf_features), mlb.transform(all_exp_features), beta=0.5, average='samples')[2])
    fout.write('f0.5-score: ' + str(precision_recall_fscore_support(mlb.transform(all_clf_features), mlb.transform(all_exp_features), beta=0.5, average='samples')[2])+'\n')

    print('Jaccard similarity:', jaccard_score(mlb.transform(all_clf_features), mlb.transform(all_exp_features), 
                                               average='samples'))
    fout.write('Jaccard similarity: ' + str(jaccard_score(mlb.transform(all_clf_features), mlb.transform(all_exp_features), 
                                               average='samples'))+'\n')
    # TODO 1: add RBO to this method
    # TODO 2: Are SHAP, Anchor outputs ordered?
    rbo_scores = []
    rbo_scores2 = []
    for clf_features, exp_features in zip(all_clf_features, all_exp_features):
#         rbo_score = rbo.RankingSimilarity(clf_features, exp_features).rbo()
#         rbo_scores.append(rbo_score)
#         print('RBO: {} {} {}'.format(rbo_score, clf_features, exp_features))
        if len(clf_features)>0 and len(exp_features)>0:
            rbo_score2 = rbo(clf_features, exp_features, p=0.5)
#             rbo_scores2.append(rbo_score2.min + rbo_score2.res/2)
            rbo_scores2.append(rbo_score2.ext)
        else:
            rbo_score2 = 0.
            rbo_scores2.append(0.)
#         print('RBO: {}'.format(rbo_score2))
#     print('RBO AVG: {}'.format(sum(rbo_scores)/len(rbo_scores)))
    print('RBO2 AVG: {}'.format(sum(rbo_scores2)/len(rbo_scores2)))
    fout.write('RBO2 AVG: {}\n'.format(sum(rbo_scores2)/len(rbo_scores2)))
    print('FIDELITY AVG: {}'.format(sum(fidelities)/len(fidelities)))
    fout.write('FIDELITY AVG: {}\n'.format(sum(fidelities)/len(fidelities)))


## Experiments

In [20]:
theNotebook = 'final_anchor' # get_notebook_name().split('.')[0]
fout = open('{}.log'.format(theNotebook), 'a', 1)
samples_range = range(1000, 6000, 1000)
print(samples_range)
# samples_range = range(100, 1100, 100)
NUM_ITERATIONS = 5
classifier_type = 'dt'
around_instance = True
_reload_libs()
xlime_mode = ["FOURTEEN"]
iteration_seed = 0

for i in range(NUM_ITERATIONS):
    iteration_seed += 1
    for dataset, dataset_info in datasets_info_dict.items():
        print('Barbe experiment started with iterations = ', i, ' Dataset: ', dataset)
        seed = iteration_seed
        gc.collect()
        
        try:
            clf = dataset_info['{}_clf'.format(classifier_type)]
            print('*** Classifier = ', clf)
            train_df = dataset_info['train_df']    #Train_df contains class label
            test_df  = dataset_info['test_df']     #Test_df contains class label
            all_features = train_df.drop('class', axis=1).columns.values
            print(train_df.head())
            
# #             # evaluate XLIME
#             for num_samples in samples_range:
#                 ouputs_clf, outputs_exp, fidelities = evaluate_explanations_parallel(dataset, clf, train_df, test_df, classifier_type, num_samples, around_instance, seed, info['max_explanation_size'], 'XLIME', xlime_mode)
#                 analyze_outputs(all_features, ouputs_clf, outputs_exp, fidelities)

#             # evaluate LIME
            for num_samples in samples_range:
                ouputs_clf, outputs_exp, fidelities = evaluate_explanations_parallel(dataset, clf, train_df, test_df, classifier_type, num_samples, around_instance, seed, info['max_explanation_size'], 'LIME')
                #analyze_outputs(all_features, ouputs_clf, outputs_exp, fidelities)

# #             # evaluate SHAP
#             for num_samples in samples_range:
#                 ouputs_clf, outputs_exp = evaluate_explanations_parallel(dataset, clf, train_df, test_df, classifier_type, num_samples, around_instance, seed, info['max_explanation_size'], 'SHAP')
#                 analyze_outputs(all_features, ouputs_clf, outputs_exp)
            
# #             # evaluate Anchors
#             for num_samples in samples_range:
#                 ouputs_clf, outputs_exp, fidelities = evaluate_explanations_parallel(dataset, clf, train_df, test_df, classifier_type, num_samples, around_instance, seed, info['max_explanation_size'], 'ANCHOR')
#                 analyze_outputs(all_features, ouputs_clf, outputs_exp, fidelities)

        except Exception as e:
            print('EXCEPTION:', str(e))
            fout.write('EXCEPTION' + str(e)+'\n')
            raise e

range(1000, 6000, 1000)
Barbe experiment started with iterations =  0  Dataset:  glass
*** Classifier =  DecisionTreeClassifier(max_depth=5,
                       random_state=RandomState(MT19937) at 0x7FDA94B4D160)
            1         2         3         4         5         6         7  \
108  1.172462  1.178967 -1.763019 -0.886022 -0.004176 -0.569697  1.663606   
206 -0.586593  1.761773 -1.763019  0.812563  0.540266 -0.705339 -0.200470   
106  3.925370 -3.049231 -1.763019  1.261614 -3.543053  0.081385  2.827836   
107  4.742401 -1.255103 -1.763019 -0.886022 -3.109974 -0.542569  4.718074   
51   0.270070 -0.226623  0.491208 -0.339351 -0.387761  0.108514  0.106939   

            8         9  class  
108 -0.369498  0.223975      2  
206  2.213128 -0.581329      7  
106  5.525627  2.237237      2  
107 -0.369498  1.834585      2  
51  -0.369498  0.525965      1  
Function evaluate_explanations_parallel with params =  glass DecisionTreeClassifier(max_depth=5,
                       ra

[[1. 1. 1. 1. 1. 1. 1. 1. 1.]
 [0. 0. 0. 1. 0. 0. 1. 1. 0.]
 [0. 1. 0. 0. 0. 1. 1. 1. 1.]] [[-5.91814038e-02  3.67610382e-01 -1.76301864e+00 -1.74507581e+00
   2.19834155e+00 -7.05339289e-01  1.31695320e+00 -3.69498000e-01
  -5.81329404e-01]
 [ 2.73194517e-01  9.08857031e-01  7.29987027e-01 -1.31547576e+00
   4.23664446e-01  1.27128680e-01  3.59817545e+00 -5.55108431e-06
   6.40005424e-02]
 [-1.17711541e+00  5.15722891e-01  5.86314162e-01 -1.07874099e+00
   2.30617698e-01  1.11021070e-05  2.71798892e+00 -5.55108431e-06
   0.00000000e+00]] False (1000, 9) (1000, 9)
Prediction going on
self.class_names [1, 2, 3, 5, 6, 7]
feature_names [1, 2, 3, 4, 5, 6, 7, 8, 9]
I guess
['-0.06', '0.37', '-1.76', '-1.75', '2.20', '-0.71', '1.32', '-0.37', '-0.58'] None
categorical_features [0, 1, 2, 3, 4, 5, 6, 7, 8]
discretized_feature_names ['-0.18 < 1 <= -0.04', '0.29 < 2 <= 0.86', '3 <= -1.76', '4 <= -1.22', '5 > 0.85', '6 <= -0.71', '7 > 0.84', '8 <= -0.37', '9 <= -0.58']
In Not Sig
Evaluating:  ((8

                       random_state=RandomState(MT19937) at 0x7FDA94B4D160)> [0] None 5 1000 euclidean None None
inside __data_inverse............ is_sparse =  False (9,)
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
first_row as discretizier is none =  [8. 7. 8. 0. 0. 2. 8. 0. 0.]
[[1. 1. 1. 1. 1. 1. 1. 1. 1.]
 [0. 0. 0. 0. 0. 0. 0. 1. 1.]
 [0. 0. 0. 0. 1. 0. 1. 1. 1.]] [[ 1.13587901e+00  3.79037944e-01  8.36450166e-01 -1.43269248e+00
  -1.13018235e+00 -4.74747599e-01  4.99376097e-01 -3.69498000e-01
  -5.81329404e-01]
 [-9.27068880e-01 -1.76155974e-01  5.91418001e-01 -3.97409355e-01
  -9.92441053e-01 -2.61208843e-01 -4.46387580e-01 -5.55108431e-06
   0.00000000e+00]
 [-2.83583121e-01 -9.76499084e-01  5.16082188e-01  7.34648736e-01
  -2.03820276e+00 -2.74760853e-01  6.76179471e-01 -5.55108431e-06
   0.00000000e+00]] False (1000, 9) (1000, 9)
Prediction going on
self.class_names

In Not Sig
Evaluating:  ((149, 1   -0.592691
2   -1.415089
3    0.619828
4   -0.202683
5    0.268045
6    0.067821
7   -0.292039
8   -0.369498
9   -0.581329
Name: 149, dtype: float64), DecisionTreeClassifier(max_depth=5,
                       random_state=RandomState(MT19937) at 0x7FDA94B4D160), 'dt', 9, 6, <lime.lime_tabular.LimeTabularExplainer object at 0x7fd9ded7e4d0>, 1000, 'ONE', 1, [1, 2, 3, 5, 6, 7], 'LIME', 5)
2 3
Inside: get_features_dt, feature =  [ 7  3  6  0  0 -2 -2  8 -2 -2  0  1 -2 -2 -2  2  1  6 -2 -2 -2  6  8 -2
 -2  1 -2 -2  4  7 -2 -2 -2]
final_features =  [8, 4, 7, 1]
----
** classes  [0, 1, 2, 3, 4, 5]
Caller 2
explain_instance [-0.59269052 -1.41508928  0.61982777 -0.20268309  0.26804516  0.06782109
 -0.29203854 -0.369498   -0.5813294 ] <bound method DecisionTreeClassifier.predict_proba of DecisionTreeClassifier(max_depth=5,
                       random_state=RandomState(MT19937) at 0x7FDA94B4D160)> [2] None 5 1000 euclidean None None
inside __data_inverse......

[[1. 1. 1. 1. 1. 1. 1. 1. 1.]
 [0. 0. 0. 0. 1. 0. 1. 1. 0.]
 [1. 1. 0. 0. 1. 0. 0. 1. 0.]] [[-5.31718047e-01 -5.35167009e-01  6.33366666e-01  3.24463785e-01
   3.54661027e-01  1.62770605e-01 -6.19069386e-01 -3.69498000e-01
   1.53259570e+00]
 [ 2.27781955e+00 -2.13538758e-01  5.96981881e-01  1.94434795e+00
   3.73192551e-01 -6.25335245e-01 -1.62008197e+00 -5.55108431e-06
   3.50015282e-01]
 [-4.08006397e-01 -6.07065708e-01  5.98853807e-01 -2.07744160e-01
   3.81826829e-01  9.91437410e-02 -2.33534874e-01 -5.55108431e-06
   8.21334211e-02]] False (1000, 9) (1000, 9)
Prediction going on
self.class_names [1, 2, 3, 5, 6, 7]
feature_names [1, 2, 3, 4, 5, 6, 7, 8, 9]
I guess
['-0.53', '-0.54', '0.63', '0.32', '0.35', '0.16', '-0.62', '-0.37', '1.53'] None
categorical_features [0, 1, 2, 3, 4, 5, 6, 7, 8]
discretized_feature_names ['-0.60 < 1 <= -0.41', '-0.70 < 2 <= -0.48', '0.61 < 3 <= 0.65', '0.23 < 4 <= 0.66', '0.28 < 5 <= 0.43', '0.14 < 6 <= 0.19', '7 <= -0.62', '8 <= -0.37', '0.59 < 9 <= 

...

[[1. 1. 1. 1. 1. 1. 1. 1. 1.]
 [0. 0. 0. 0. 0. 0. 0. 0. 1.]
 [0. 0. 1. 0. 1. 0. 1. 0. 0.]] [[-0.49818319 -0.60373238  0.64690557  0.3635117   0.57738753  0.17633482
  -0.64523185 -0.369498   -0.5813294 ]
 [ 0.09470223 -0.17069401  0.         -0.48972314 -0.92661045  0.12297739
  -0.11944065  0.0409689   0.        ]
 [-0.27800224 -1.00582588  0.60842272 -1.76951937  0.5330787  -0.56707116
  -1.10977649  0.33606523  2.316071  ]] False (5000, 9) (5000, 9)
Prediction going on
self.class_names [1, 2, 3, 5, 6, 7]
feature_names [1, 2, 3, 4, 5, 6, 7, 8, 9]
I guess
['-0.50', '-0.60', '0.65', '0.36', '0.58', '0.18', '-0.65', '-0.37', '-0.58'] None
categorical_features [0, 1, 2, 3, 4, 5, 6, 7, 8]
discretized_feature_names ['-0.60 < 1 <= -0.41', '-0.70 < 2 <= -0.48', '0.61 < 3 <= 0.65', '0.23 < 4 <= 0.66', '0.43 < 5 <= 0.66', '0.14 < 6 <= 0.19', '7 <= -0.62', '8 <= -0.37', '9 <= -0.58']
In Not Sig
Evaluating:  ((146, 1   -0.208564
2    0.287617
3    0.714600
4   -0.671258
5    0.119561
6   -0.5561

[[1. 1. 1. 1. 1. 1. 1. 1. 1.]
 [0. 0. 0. 0. 0. 0. 0. 1. 1.]
 [0. 0. 0. 1. 0. 0. 1. 1. 1.]] [[-2.56465452e-02  1.21324996e+00 -2.46661835e-01  3.24463785e-01
  -3.63013271e-01 -7.05339289e-01  1.85426488e-01 -3.69498000e-01
  -5.81329404e-01]
 [-7.57577357e-02  2.66187437e-01  2.84248717e-01  2.44123434e+00
   6.41527250e-02 -4.17047591e-02 -2.56495131e-02 -5.55108431e-06
   0.00000000e+00]
 [-3.60157669e-01 -1.93145655e-01  0.00000000e+00  4.54618712e-01
   5.25245466e-01 -6.55091719e-01  6.28689075e-02 -5.55108431e-06
   0.00000000e+00]] False (5000, 9) (5000, 9)
Prediction going on
self.class_names [1, 2, 3, 5, 6, 7]
feature_names [1, 2, 3, 4, 5, 6, 7, 8, 9]
I guess
['-0.03', '1.21', '-0.25', '0.32', '-0.36', '-0.71', '0.19', '-0.37', '-0.58'] None
categorical_features [0, 1, 2, 3, 4, 5, 6, 7, 8]
discretized_feature_names ['-0.04 < 1 <= 0.18', '2 > 1.19', '-1.76 < 3 <= 0.01', '0.23 < 4 <= 0.66', '-0.40 < 5 <= -0.01', '6 <= -0.71', '0.06 < 7 <= 0.39', '8 <= -0.37', '9 <= -0.58']
In No

[[1. 1. 1. 1. 1. 1. 1. 1. 1.]
 [0. 0. 0. 0. 0. 1. 0. 1. 0.]
 [0. 0. 0. 0. 0. 0. 0. 1. 0.]] [[ 5.56640544e-01  6.64726992e-01 -8.49142885e-01  3.43987744e-01
  -1.13018235e+00 -1.76334822e-01  1.03570668e+00 -3.69498000e-01
   1.23060640e+00]
 [ 6.33307801e-02 -7.99314591e-01  5.43259863e-01 -4.56684137e-01
   7.75330586e-02 -2.67985304e-01  1.81988644e-01 -5.55108431e-06
  -1.33772876e-01]
 [-2.97056682e-01  1.99280325e+00  2.86664224e-01 -1.11519535e-01
   6.60133367e-01  1.49933110e-01 -2.54941326e-01 -5.55108431e-06
   0.00000000e+00]] False (5000, 9) (5000, 9)
Prediction going on
self.class_names [1, 2, 3, 5, 6, 7]
feature_names [1, 2, 3, 4, 5, 6, 7, 8, 9]
I guess
['0.56', '0.66', '-0.85', '0.34', '-1.13', '-0.18', '1.04', '-0.37', '1.23'] None
categorical_features [0, 1, 2, 3, 4, 5, 6, 7, 8]
discretized_feature_names ['0.18 < 1 <= 0.96', '0.29 < 2 <= 0.86', '-1.76 < 3 <= 0.01', '0.23 < 4 <= 0.66', '5 <= -1.09', '-0.46 < 6 <= -0.05', '7 > 0.84', '8 <= -0.37', '0.59 < 9 <= 1.83']
In

[[1. 1. 1. 1. 1. 1. 1. 1. 1.]
 [0. 1. 0. 0. 0. 1. 0. 1. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0.]] [[-1.14056627e-01  3.56182820e-01  8.97375216e-01  1.68272117e-01
  -1.06831387e+00  2.71284342e-02 -5.01338282e-01 -3.69498000e-01
   9.28617099e-01]
 [ 3.70945192e-01  4.58621565e-01  7.51415288e-01  8.86132987e-01
   1.30966008e+00  3.74121888e-02 -2.80053650e-01 -5.55108431e-06
   0.00000000e+00]
 [ 1.74614695e-02 -8.05590785e-01  0.00000000e+00 -5.60935899e-01
  -5.17926483e-01 -2.00009745e-01  4.04808174e+00  2.31248189e+00
   0.00000000e+00]] False (5000, 9) (5000, 9)
Prediction going on
self.class_names [1, 2, 3, 5, 6, 7]
feature_names [1, 2, 3, 4, 5, 6, 7, 8, 9]
I guess
['-0.11', '0.36', '0.90', '0.17', '-1.07', '0.03', '-0.50', '-0.37', '0.93'] None
categorical_features [0, 1, 2, 3, 4, 5, 6, 7, 8]
discretized_feature_names ['-0.18 < 1 <= -0.04', '0.29 < 2 <= 0.86', '3 > 0.77', '-0.02 < 4 <= 0.23', '-1.09 < 5 <= -0.62', '-0.05 < 6 <= 0.05', '-0.62 < 7 <= -0.48', '8 <= -0.37', '0.59 < 9 <

[[1. 1. 1. 1. 1. 1. 1. 1. 1.]
 [0. 0. 0. 0. 0. 0. 1. 1. 1.]
 [0. 0. 0. 0. 0. 0. 0. 0. 1.]] [[-4.49405213e-01 -7.80645323e-02  6.33366666e-01  3.04939827e-01
  -1.65034154e-01  2.17027474e-01 -5.66744451e-01 -3.69498000e-01
  -5.81329404e-01]
 [-2.32247507e-01 -3.98260409e-01  5.32272190e-01  2.14662450e+00
   5.51907896e-01  6.29855561e-03 -5.46318262e-01 -5.55108431e-06
   0.00000000e+00]
 [-6.89239604e-01  9.26220744e-01  0.00000000e+00 -5.41142728e-02
   1.79862308e-02 -5.74200792e-01 -7.02332522e-01 -2.74839192e-02
   0.00000000e+00]] False (5000, 9) (5000, 9)
Prediction going on
self.class_names [1, 2, 3, 5, 6, 7]
feature_names [1, 2, 3, 4, 5, 6, 7, 8, 9]
I guess
['-0.45', '-0.08', '0.63', '0.30', '-0.17', '0.22', '-0.57', '-0.37', '-0.58'] None
categorical_features [0, 1, 2, 3, 4, 5, 6, 7, 8]
discretized_feature_names ['-0.60 < 1 <= -0.41', '-0.16 < 2 <= 0.03', '0.61 < 3 <= 0.65', '0.23 < 4 <= 0.66', '-0.40 < 5 <= -0.01', '6 > 0.19', '-0.62 < 7 <= -0.48', '8 <= -0.37', '9 <= -0.5

In [21]:
print('abc')

abc


fourteen and then fifteen: 0.5, and then 0

with pruning

In [22]:
### 0.1 * softmax
np.arange(1.,0,-.1)

array([1. , 0.9, 0.8, 0.7, 0.6, 0.5, 0.4, 0.3, 0.2, 0.1])

In [23]:
df = pd.DataFrame({'age':    [ 3,  29],
                   'height': [94, 170],
                   'weight': [31, 115]})
df

age  height  weight
0    3      94      31
1   29     170     115

In [24]:
df.columns.values

array(['age', 'height', 'weight'], dtype=object)

In [25]:
df.values

array([[  3,  94,  31],
       [ 29, 170, 115]])